# Validation report

This notebook is used to prototype the script that generates the validation report for a given date.

The idea is that takes the path to some data of a test, process it, runs the models and generates the validation information and visualization to generate the report.

The report is located in the [docs](docs/validation) folder

The indexes: `start_idx`, `end_idx` and `span` are used to define the range of the data to be used for the validation. Make sure to define them properly together with the sample time.

To export the `YYYYMMDD_MED.csv` data complementary to the `YYYYMMDD_solarMED.csv` data the notebook [test_data_to_csv.ipynb](/home/jmserrano/Nextcloud/Juanmi_MED_PSA/Python) is used.


> [!warning] Report will get overtwritten
> In the last step of this notebook, the report is saved in the `docs` folder, if the report already exists, it will be overwritten.

In [16]:
from pathlib import Path
import os
import hjson
import numpy as np
import pandas as pd
from IPython.display import display
from loguru import logger
import time
import datetime
import json
import copy

# Visualization
from phd_visualizations.test_timeseries import experimental_results_plot
from phd_visualizations import save_figure
from phd_visualizations.constants import generate_plotly_config

#
from solarMED_modeling.data_validation import within_range_or_nan_or_max, within_range_or_zero_or_max
from solarMED_modeling.utils import data_conditioning, data_preprocessing


# Setup environment for running MATLAB code if not done externally
# os.environ["MR"] = f"{os.environ['HOME']}/PSA/MATLAB_runtime/R2023b"
os.environ["MR"] = f"{os.environ['HOME']}/MATLAB/R2023b"
MR = os.environ["MR"]
os.environ["LD_LIBRARY_PATH"] = f"{MR}/runtime/glnxa64:{MR}/bin/glnxa64:{MR}/sys/os/glnxa64:{MR}/sys/opengl/lib/glnxa64"

# auto reload modules
%load_ext autoreload
%autoreload 2

# Paths definition
data_path: Path = Path(f'{os.getenv("HOME")}/Nextcloud/Juanmi_MED_PSA/EURECAT/data')
config_path: Path = Path(f'{os.getenv("HOME")}/development_psa/models_psa/data')
output_path: Path = Path(f'{os.getenv("HOME")}/development_psa/models_psa/docs/validation')

test_date_str = "20230703"

# Data filenames
filename_process_data = f'{test_date_str}_solarMED.csv'
filename_process_data2 = f'{test_date_str}_MED.csv'

# Resample figures using plotly_resampler
resample_figures = False

sample_rate = '30s'
sample_rate_numeric = int(sample_rate[:-1])

# Parameters
cost_w: float = 3 # €/m³, cost of water
cost_e: float = 0.05 # €/kWh, cost of electricity

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Pre-processing

In [17]:
data_paths = [data_path / filename_process_data, data_path / filename_process_data2]

# Load variables information
with open( config_path / 'variables_config.hjson') as f:
    vars_config = hjson.load(f)

df = data_preprocessing(paths=data_paths, sample_rate_key=sample_rate, vars_config=vars_config)

2024-05-09 16:57:41.602 | DEBUG    | solarMED_modeling.utils:process_dataframe:68 - Index([], dtype='object')
2024-05-09 16:57:41.605 | INFO     | solarMED_modeling.utils:process_dataframe:75 - Number of duplicate index values in df: 0
2024-05-09 16:57:41.953 | DEBUG    | solarMED_modeling.utils:process_dataframe:68 - Index([], dtype='object')
2024-05-09 16:57:41.955 | INFO     | solarMED_modeling.utils:process_dataframe:75 - Number of duplicate index values in df: 0
2024-05-09 16:57:42.467 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-003 not found in dataframe columns.
2024-05-09 16:57:42.478 | DEBUG    | phd_visualizations.utils.units:unit_conversion:552 - Updated Tamb to C from C
2024-05-09 16:57:42.480 | DEBUG    | phd_visualizations.utils.units:unit_conversion:552 - Updated Tmed_c_in to C from C
2024-05-09 16:57:42.481 | DEBUG    | phd_visualizations.utils.units:unit_conversion:552 - Updated Tmed_s_in to C from C
2024-05-09 16:57:42.483 |

### Add / modify variables

In [18]:
df = data_conditioning(df, cost_e=cost_e, cost_w=cost_w, sample_rate_numeric=sample_rate_numeric)

2024-05-09 16:57:44.386 | INFO     | solarMED_modeling.utils:data_conditioning:214 - Heat exchanger secondary flow rate estimated successfully.
2024-05-09 16:57:44.438 | INFO     | solarMED_modeling.utils:data_conditioning:244 - Thermal storage discharge flow rate estimated successfully (qts_dis/q3wv_src).
2024-05-09 16:57:44.441 | INFO     | solarMED_modeling.utils:data_conditioning:254 - Auxiliary variables calculated successfully.
2024-05-09 16:57:45.766 | INFO     | solarMED_modeling.utils:data_conditioning:261 - Solar field power calculated successfully.
2024-05-09 16:57:48.420 | INFO     | solarMED_modeling.utils:data_conditioning:268 - Thermal storage power calculated successfully.
/home/jmserrano/development_psa/models_psa/solarMED_modeling/utils/__init__.py:272: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. 

In [19]:
# Make sure the output folders exist
# - output_path/YYYYMMDD
# - output_path/YYYYMMDD/attachments

date_str = df.index[0].strftime("%Y%m%d")

output_folder = output_path / date_str
attachments_folder = output_folder / 'attachments'

output_folder.mkdir(parents=True, exist_ok=True)
attachments_folder.mkdir(parents=True, exist_ok=True)

## Visualize test data


In [5]:
# Generate visualization

# Load plot configuration
with open( config_path / "plot_config.hjson") as f:
    plt_config = hjson.load(f)

fig = experimental_results_plot(plt_config, df, vars_config=vars_config, resample=resample_figures)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'solar_med_{df.index[0].strftime("%Y%m%d")}')
# )

# Save figure
save_figure(
    figure_name=f"{date_str}_solarMED_visualization", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

2024-05-09 15:34:14.171 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:34:14.172 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tamb
2024-05-09 15:34:14.173 | DEBUG    | phd_visualizations.test_timeseries:add_trace:75 - legend_id: global_legend, legend: legend for trace T<sub>amb</sub>
2024-05-09 15:34:14.190 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>amb</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: False
2024-05-09 15:34:14.196 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tmed_c_in
2024-05-09 15:34:14.197 | DEBUG    | phd_visualizations.test_timeseries:add_trace:75 - legend_id: global_legend, legend: legend for trace T<sub>med,c,in</sub> (⁰C)
2024-05-09 15:34:14.202 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>m

## Complete system

Better to start from the complete system, and use its parameters to validate the individual components.

In [20]:
# Evaluate model

from solarMED_modeling.solar_med import SolarMED

idx_start = int(round(700 / sample_rate_numeric, 0)) # 10 minutes
span = int(round(700 / sample_rate_numeric, 0)) # 10 minutes
idx_end = len(df)
df_mod = pd.DataFrame()

# Initialize model
model = SolarMED(
    sample_time=sample_rate_numeric,
    resolution_mode='simple',
    use_models=True,
    use_finite_state_machine=True,
    
    # Initial states
    ## Thermal storage
    Tts_h=[df['Tts_h_t'].iloc[idx_start], df['Tts_h_m'].iloc[idx_start], df['Tts_h_b'].iloc[idx_start]], 
    Tts_c=[df['Tts_c_t'].iloc[idx_start], df['Tts_c_m'].iloc[idx_start], df['Tts_c_b'].iloc[idx_start]],
    
    ## Solar field
    Tsf_in_ant=df['Tsf_in'].iloc[idx_start-span:idx_start].values,
    msf_ant=df['qsf'].iloc[idx_start-span:idx_start].values,
    
    cost_w = cost_w, # €/m³ 
    cost_e = cost_e # €/kWhe
)


2024-05-09 16:57:52.106 | INFO     | solarMED_modeling.solar_med:init_matlab_engine:701 - MATLAB engine initialized
2024-05-09 16:57:52.116 | INFO     | solarMED_modeling.solar_med:model_post_init:522 - 
        SolarMED model initialized with: 
            - Evaluating models: True
            - Evaluating finite state machines: True
            - Resolution mode: simple
            - Sample time: 30.0 s
            - MED actuators: ['med_brine_pump', 'med_feed_pump', 'med_distillate_pump', 'med_cooling_pump', 'med_heatsource_pump']
            - Solar field actuators: ['sf_pump']
            - Thermal storage actuators: ['ts_src_pump']
        


In [21]:

# Run model
# %autoreload 2

for idx in range(idx_start, idx_end):
    # idx = 1
    ds = df.iloc[idx]
    
    start_time = time.time()
        
    model.step(
        # Decision variables
        ## MED
        mmed_s=ds['qmed_s'],
        mmed_f=ds['qmed_f'],
        Tmed_s_in=ds['Tmed_s_in'],
        Tmed_c_out=ds['Tmed_c_out'],
        ## Thermal storage
        mts_src=ds['qhx_s'],
        ## Solar field
        Tsf_out=ds['Tsf_out'],
        
        # Inputs
        # When the solar field is starting up, a flow can be provided to sync the model with the real system, if a valid Tsf_out is provided, it will be prioritized
        msf=ds['qsf'] if ds['qsf'] > 4 else None,
        
        # Environment variables
        Tmed_c_in=ds['Tmed_c_in'],
        Tamb=ds['Tamb'],
        I=ds['I'],
    )
    
    logger.info(f"Finished Iteration {idx} / {idx_end} - {df.index[idx]:%H:%M:%S}, elapsed time: {time.time()-start_time:.2f} seconds.")

    df_mod = model.to_dataframe(df_mod)
    
# Create a copy of the dataframe to use it later
df_mod_copy = copy.deepcopy(df_mod)
    

2024-05-09 16:57:52.324 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (mmed_s_sp) Value 0.03 is less than 30.00 -> 0.0
2024-05-09 16:57:52.325 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (mmed_f_sp) Value 0.82 is less than 5.00 -> 0.0
2024-05-09 16:57:52.326 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (Tmed_s_in_sp) Value 29.34 is less than 60.00 -> 0.0
2024-05-09 16:57:52.328 | DEBUG    | solarMED_modeling.data_validation:within_range_or_min_or_max:69 - (Tmed_c_out_sp) Value 23.64 is less than 24.10 -> 24.10
2024-05-09 16:57:52.329 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (mts_src_sp) Value 0.00 is less than 0.95 -> 0.0
2024-05-09 16:57:52.329 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (Tsf_out_sp) Value 51.65 is less than 65.00 -> 0.0
2024-05-09 16:57:52.330 | DEBUG    | solarMED_modeling.solar_med:step:6

In [8]:
# Generate visualization

# Load plot configuration
with open( config_path / "plot_config_validation.hjson") as f:
    plt_config = hjson.load(f)

# Sync model index with measured data
df_mod.index = df.index[idx_start:idx if idx<idx_end-1 else idx_end]

fig = experimental_results_plot(plt_config, df, df_comp=df_mod, vars_config=vars_config, resample=resample_figures)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'solar_med_{df.index[0].strftime("%Y%m%d")}')
# )

# Save figure
save_figure(
    figure_name=f"{date_str}_SolarMED_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'), 
    width=fig.layout.width, height=fig.layout.height, scale=2
)

2024-05-09 15:36:03.898 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:36:03.900 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tamb
2024-05-09 15:36:03.900 | DEBUG    | phd_visualizations.test_timeseries:add_trace:75 - legend_id: global_legend, legend: legend for trace T<sub>amb</sub>
2024-05-09 15:36:03.902 | WARNING  | phd_visualizations.test_timeseries:add_trace:136 - Index of comparison dataframe 0 is not the same as the main dataframe, filling difference with NaNs
2024-05-09 15:36:03.920 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>amb</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:36:03.922 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tmed_c_in
2024-05-09 15:36:03.922 | DEBUG    | phd_visualizations.test_timeseries:add_tr

## Finite state machines

In [9]:
from solarMED_modeling import SF_TS_State, MedState
from solarMED_optimization.path_exploration import Node, generate_edges, generate_edges_dataframe
from solarMED_optimization.visualization import plot_state_graph

Np = len(df_mod)

# Generate nodes dataframes
nodes_sfts_df = pd.DataFrame([
    Node(step_idx=step_idx,state=state).model_dump()
    for step_idx in range(Np) for state in [state for state in SF_TS_State]
])
nodes_med_df = pd.DataFrame([
    Node(step_idx=step_idx, state=state).model_dump()
    for step_idx in range(Np) for state in [state for state in MedState]
])

# Generate edges dataframes
edges_list_med = []; edges_list_sfts = []
for step_idx in range(Np):
    edges_list_med = generate_edges(edges_list_med, step_idx, system='MED', Np=Np)
    edges_list_sfts = generate_edges(edges_list_sfts, step_idx, system='SFTS', Np=Np)
    
edges_df_med = generate_edges_dataframe(edges_list_med, nodes_df=nodes_med_df)
edges_df_sfts = generate_edges_dataframe(edges_list_sfts, nodes_df=nodes_sfts_df)


fig = plot_state_graph(
    nodes_df=[nodes_sfts_df, nodes_med_df], 
    system='SolarMED',
    # edges_df=[edges_df_sfts, edges_df_med],
    results_df=df_mod,
    Np=Np, 
    height=800,
    width=1200,
)

# Save figure
save_figure(
    figure_name=f"{date_str}_SolarMED_FSMs", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'), 
    width=fig.layout.width, height=fig.layout.height, scale=2
)

2024-05-09 15:38:27.090 | WARNING  | solarMED_optimization.visualization:plot_state_graph:81 - There are more samples than the maximum specified (30), states will be shown every 42 samples. Aliasing may occur


FigureWidget({
    'data': [{'hoverinfo': 'text',
              'line': {'color': 'rgb(50,50,50)', 'width': 0.5},
              'marker': {'color': '#ff7800', 'size': 20, 'symbol': 'circle-dot'},
              'mode': 'markers',
              'name': 'states',
              'text': array(['IDLE', 'RECIRCULATING_TS', 'HEATING_UP_SF', ..., 'RECIRCULATING_TS',
                             'HEATING_UP_SF', 'SF_HEATING_TS'], dtype=object),
              'type': 'scatter',
              'uid': '5517d998-ad42-452e-940a-1254dc1005c7',
              'x': [0, 0, 0, 0, 42, 42, 42, 42, 84, 84, 84, 84, 126, 126, 126,
                    126, 168, 168, 168, 168, 210, 210, 210, 210, 252, 252, 252,
                    252, 294, 294, 294, 294, 336, 336, 336, 336, 378, 378, 378,
                    378, 420, 420, 420, 420, 462, 462, 462, 462, 504, 504, 504,
                    504, 546, 546, 546, 546, 588, 588, 588, 588, 630, 630, 630,
                    630, 672, 672, 672, 672, 714, 714, 714, 714, 756

## Thermal storage

In [10]:
# Evaluate model

from solarMED_modeling.thermal_storage import thermal_storage_two_tanks_model

df_ts = df.copy()

# # Define idx_start as the first index non nan for:
# idxs_start = [df_ts.index.get_loc( df_ts['Tts_h_t'].first_valid_index()),
#               df_ts.index.get_loc( df_ts['Tts_h_out'].first_valid_index()),
#               df_ts.index.get_loc( df_ts['Tts_c_b_in'].first_valid_index())]
# idx_start = np.max(idxs_start)
# 
# # Remove all nan for Tts_h_t
# df_ts = df_ts[df_ts['Tts_h_t'].notna()]
# df_ts = df_ts[df_ts['Tts_c_b_in'].notna()]

idx_start = 0
idx_end = len(df_ts)

# idx_start = 0

Th_labels = ['Tts_h_t', 'Tts_h_m', 'Tts_h_b']
Tc_labels = ['Tts_c_t', 'Tts_c_m', 'Tts_c_b']

N = len(Th_labels)
    
df_mod = pd.DataFrame()

Tts_h = np.zeros((idx_end-idx_start+1, N), dtype=float)
Tts_c = np.zeros((idx_end-idx_start+1, N), dtype=float)

Tts_h[0] = np.array( [df_ts.iloc[idx_start][T] for T in Th_labels] )
Tts_c[0] = np.array( [df_ts.iloc[idx_start][T] for T in Tc_labels] )
for idx in range(idx_start, idx_end):
    
    j = idx-idx_start+1
    ds = df_ts.iloc[idx]
        
    # logger.info(f"Iteration {idx} / {idx_end}")
    start_time = time.time()
    
    Tts_h[j], Tts_c[j] = thermal_storage_two_tanks_model(
        Ti_ant_h=Tts_h[j-1], Ti_ant_c=Tts_c[j-1],  # [ºC], [ºC]
        Tt_in=ds["Tts_h_in"],  # ºC
        Tb_in=ds["Tts_c_in"],  # ºC
        Tamb=ds["Tamb"],  # ºC

        qsrc=ds["qts_src"],  # m³/h
        qdis=ds["qts_dis"],  # m³/h

        UA_h=model.UAts_h,  # W/K
        UA_c=model.UAts_c,  # W/K
        Vi_h=model.Vts_h,  # m³
        Vi_c=model.Vts_c,  # m³
        ts=sample_rate_numeric, Tmin=60  # seg, ºC
    )
    
    out = {label: Tts_h[j][i] for i, label in enumerate(Th_labels)}
    out.update({label: Tts_c[j][i] for i, label in enumerate(Tc_labels)})
    
    result = pd.DataFrame(out, index=[0])
    
    logger.info(f"Finished iteration {idx} / {idx_end}, elapsed time: {time.time()-start_time:.2f} s")
    
    df_mod = pd.concat([df_mod, result], ignore_index=True)

2024-05-09 15:23:37.175 | INFO     | __main__:<module>:63 - Finished iteration 0 / 1280, elapsed time: 0.02 s
2024-05-09 15:23:37.192 | INFO     | __main__:<module>:63 - Finished iteration 1 / 1280, elapsed time: 0.02 s
2024-05-09 15:23:37.210 | INFO     | __main__:<module>:63 - Finished iteration 2 / 1280, elapsed time: 0.02 s
2024-05-09 15:23:37.229 | INFO     | __main__:<module>:63 - Finished iteration 3 / 1280, elapsed time: 0.02 s
2024-05-09 15:23:37.256 | INFO     | __main__:<module>:63 - Finished iteration 4 / 1280, elapsed time: 0.03 s
2024-05-09 15:23:37.289 | INFO     | __main__:<module>:63 - Finished iteration 5 / 1280, elapsed time: 0.03 s
2024-05-09 15:23:37.328 | INFO     | __main__:<module>:63 - Finished iteration 6 / 1280, elapsed time: 0.04 s
2024-05-09 15:23:37.368 | INFO     | __main__:<module>:63 - Finished iteration 7 / 1280, elapsed time: 0.04 s
2024-05-09 15:23:37.394 | INFO     | __main__:<module>:63 - Finished iteration 8 / 1280, elapsed time: 0.02 s
2024-05-09

In [11]:
# Generate visualization

# Load plot configuration
with open(config_path / 'plt_config_thermal_storage.json') as f:
    plt_config = json.load(f)
    
# Sync model index with measured data
df_mod.index = df_ts.index[idx_start:idx if idx < idx_end - 1 else idx_end]

fig = experimental_results_plot(plt_config, df_ts, df_comp=[df_mod], vars_config=vars_config, resample=resample_figures)

# Save figure
save_figure(
    figure_name=f"{date_str}_thermal_storage_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'{date_str}_thermal_storage_validation')
# )

2024-05-09 15:24:28.621 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:24:28.622 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qts_dis
2024-05-09 15:24:28.634 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace q<sub>ts,dis</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:24:28.635 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qts_src
2024-05-09 15:24:28.647 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace q<sub>ts,src</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:24:28.649 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Pts_src
2024-05-09 15:24:28.706 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace P<sub>ts,src</sub> added in 

## Solar field

In [12]:
# Evaluate model

from solarMED_modeling.solar_field import solar_field_model

idx_start = int(round(700 / sample_rate_numeric, 0)) # 10 minutes
span = int(round(700 / sample_rate_numeric, 0)) # 10 minutes

if span > idx_start:
    logger.warning(f'Span {span} cant be greater than idx_start {idx_start}. Setting span to idx_start')
    span = idx_start

# Initialize result vectors
# q_sf_mod   = np.zeros(len(df), dtype=float)
Tsf_out_mod_delay   = np.zeros(len(df)-idx_start, dtype=float)
# l   = np.zeros(len(df), dtype=float)


# Evaluate model
# Tsf_out_mod[0:idx_start] = df.iloc[0:idx_start]['Tsf_out']
# Tsf_out_mod_delay[0:idx_start] = df.iloc[0:idx_start]['Tsf_out']

Tsf_out_mod_delay[0] = df.iloc[idx_start]['Tsf_out']
for i in range(idx_start+1, len(df)):
    # solar_field_model(Tin: conHotTemperatureType, q: PositiveFloat, I: PositiveFloat, Tamb: float,
    #                   Tout_ant: float, q_ant: np.ndarray[float] = None,
    #                   beta: float = 0.0975, H: float = 2.2, nt=1, np=7 * 5, ns=2, Lt=1.15 * 20, Acs:float= 7.85e-5,
    #                   sample_time=1) -> float:
    ds = df.iloc[i]
    j = i-idx_start
    
    
    start_time = time.time()
    
    Tsf_out_mod_delay[j] = solar_field_model(
        Tin=df.iloc[i-span:i]['Tsf_in'].values, # From current value, up to idx_start samples before 
        q=df.iloc[i:i-span:-1]['qsf'].values, # From current value, up to idx_start samples before, in reverse order
        I=ds['I'], Tamb=ds['Tamb'],  Tout_ant=Tsf_out_mod_delay[j-1],
        sample_time=sample_rate_numeric, consider_transport_delay=True,
        # Model parameters
        # beta=1.1578e-2, H=3.1260, gamma=0.0471
        beta=model.beta_sf, H=model.H_sf, gamma=model.gamma_sf
    )
    
    logger.info(f"Iteration {i} / {len(df)}. Elapsed time: {time.time()-start_time:.2f} s")
    
df_mod = pd.DataFrame(Tsf_out_mod_delay, columns=['Tsf_out'], index=df.index[idx_start:])

2024-05-09 15:25:08.460 | INFO     | __main__:<module>:44 - Iteration 24 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.463 | INFO     | __main__:<module>:44 - Iteration 25 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.466 | INFO     | __main__:<module>:44 - Iteration 26 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.471 | INFO     | __main__:<module>:44 - Iteration 27 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.475 | INFO     | __main__:<module>:44 - Iteration 28 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.478 | INFO     | __main__:<module>:44 - Iteration 29 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.480 | INFO     | __main__:<module>:44 - Iteration 30 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.484 | INFO     | __main__:<module>:44 - Iteration 31 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.488 | INFO     | __main__:<module>:44 - Iteration 32 / 1280. Elapsed time: 0.00 s
2024-05-09 15:25:08.491 | INFO     | __main__:<module>:44 - Iteration 33 / 1280. E

In [13]:
# Generate visualization

# Load plot configuration
with open(config_path / 'plt_config_solar_field.json') as f:
    plt_config = json.load(f)

# Sync model index with measured data
df_mod.index = df.index[idx_start:i if i < idx_end - 1 else idx_end]

fig = experimental_results_plot(plt_config, df, df_comp=[df_mod], vars_config=vars_config, resample=resample_figures)

# Save figure
save_figure(
    figure_name=f"{date_str}_solar_field_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'{date_str}_solar_field_validation')
# )

2024-05-09 15:25:17.452 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:25:17.454 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tamb
2024-05-09 15:25:17.461 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>amb</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:25:17.463 | DEBUG    | phd_visualizations.test_timeseries:experimental_results_plot:700 - Adding trace I to right yaxis 2
2024-05-09 15:25:17.463 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add I
2024-05-09 15:25:17.474 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace I (W/m<sup>2</sup>) added in yaxis2 (right), row 1, uncertainty: False, comparison: True
2024-05-09 15:25:17.477 | DEBUG    | phd_visualizations.test_timeseries:experimental_results_plot:611 - Found

In [14]:
# Evaluate model (inverse)

from solarMED_modeling.solar_field import solar_field_inverse_model

df_on = df.where(df['Tsf_out']-df['Tsf_in']>4).dropna()

idx_start = int(round(700 / sample_rate_numeric, 0)) # 10 minutes
span = int(round(700 / sample_rate_numeric, 0)) # 10 minutes

if span > idx_start:
    logger.warning(f'Span {span} cant be greater than idx_start {idx_start}. Setting span to idx_start')
    span = idx_start
    
# Initialize result vectors
# q_sf_mod   = np.zeros(len(df), dtype=float)
qsf_mod   = np.zeros(len(df_on)-idx_start+span, dtype=float)
# l   = np.zeros(len(df), dtype=float)

# Evaluate model
qsf_mod[0:span] = df_on.iloc[idx_start-span:idx_start]['qsf']
# qsf_mod[0:idx_start] = df_on.iloc[0:idx_start]['qsf']
for i in range(idx_start, len(df_on)):
    # solar_field_model(Tin: conHotTemperatureType, q: PositiveFloat, I: PositiveFloat, Tamb: float,
    #                   Tout_ant: float, q_ant: np.ndarray[float] = None,
    #                   beta: float = 0.0975, H: float = 2.2, nt=1, np=7 * 5, ns=2, Lt=1.15 * 20, Acs:float= 7.85e-5,
    #                   sample_time=1) -> float:
    ds = df_on.iloc[i]
    j=i-(idx_start-span)
    
    start_time = time.time()
    
    qsf_mod[j] =solar_field_inverse_model(
        Tin=df_on.iloc[i-span:i]['Tsf_in'].values, 
        Tout=ds['Tsf_out'], I=ds['I'], Tamb=ds['Tamb'],
        Tout_ant=df_on.iloc[i-1]['Tsf_out'],
        q_ant=qsf_mod[j:j-span:-1],
        sample_time=sample_rate_numeric, consider_transport_delay=True, 
        filter_signal=True, f=0.1,
        # Model parameters
        beta=model.beta_sf, H=model.H_sf, gamma=model.gamma_sf,
    )
    
    logger.info(f"Iteration {i} / {len(df_on)}, elapsed time: {time.time()-start_time:.2f} s")
    

# Remove the  span samples, since they are not really predictions from the model
# qsf_mod = qsf_mod[span:]

# Create a dataframe for both the original and filtered data
df_mod = pd.DataFrame({'qsf': qsf_mod}, index=df_on.index)

2024-05-09 15:25:31.726 | INFO     | __main__:<module>:43 - Iteration 23 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.728 | INFO     | __main__:<module>:43 - Iteration 24 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.730 | INFO     | __main__:<module>:43 - Iteration 25 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.732 | INFO     | __main__:<module>:43 - Iteration 26 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.734 | INFO     | __main__:<module>:43 - Iteration 27 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.736 | INFO     | __main__:<module>:43 - Iteration 28 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.738 | INFO     | __main__:<module>:43 - Iteration 29 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.739 | INFO     | __main__:<module>:43 - Iteration 30 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.741 | INFO     | __main__:<module>:43 - Iteration 31 / 739, elapsed time: 0.00 s
2024-05-09 15:25:31.743 | INFO     | __main__:<module>:43 - Iteration 32 / 739, elapsed tim

In [15]:
# Generate visualization (inverse model)

# Load plot configuration
with open(config_path / 'plt_config_solar_field.json') as f:
    plt_config = json.load(f)

# Sync model index with measured data
# df_mod.index = df_on.index[idx_start:i if i < idx_end - 1 else idx_end]
df_mod.index = df_on.index

fig = experimental_results_plot(plt_config, df_on, df_comp=[df_mod], vars_config=vars_config, resample=resample_figures)

# Save figure
save_figure(
    figure_name=f"{date_str}_solar_field_inverse_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'{date_str}_solar_field_inverse_validation')
# )

2024-05-09 15:25:41.182 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:25:41.184 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tamb
2024-05-09 15:25:41.192 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>amb</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:25:41.195 | DEBUG    | phd_visualizations.test_timeseries:experimental_results_plot:700 - Adding trace I to right yaxis 2
2024-05-09 15:25:41.196 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add I
2024-05-09 15:25:41.204 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace I (W/m<sup>2</sup>) added in yaxis2 (right), row 1, uncertainty: False, comparison: True
2024-05-09 15:25:41.207 | DEBUG    | phd_visualizations.test_timeseries:experimental_results_plot:611 - Found

## Heat exchanger

In [16]:
# Evaluate model

from solarMED_modeling.heat_exchanger import heat_exchanger_model, calculate_heat_transfer_effectiveness

df["epsilon"] = np.nan

df_mod = pd.DataFrame()

# Run model
for idx in range(idx_start,idx_end):
    
    ds = df.iloc[idx]
        
    # logger.info(f"Iteration {idx} / {idx_end}")
    start_time = time.time()
    
    Thx_p_in = ds['Thx_p_in']
    Thx_s_in = ds['Thx_s_in']
    qhx_p = within_range_or_zero_or_max(ds['qhx_p'], range=[5, 10])
    # qhx_s = within_range_or_zero_or_max(ds['qhx_s'], range=[0.9, 1.7])
    qhx_s = ds['qhx_s']
    Tamb = ds['Tamb']
    
    Thx_p_out, Thx_s_out, epsilon = heat_exchanger_model(Tp_in=Thx_p_in, Ts_in=Thx_s_in, qp=qhx_p, qs=qhx_s, Tamb=Tamb, UA=model.UA_hx, H=model.H_hx, return_epsilon=True)
    
    try:
        estimated_epsilon = calculate_heat_transfer_effectiveness(Tp_in=Thx_p_in, Tp_out=ds["Thx_p_out"], Ts_in=Thx_s_in, Ts_out=ds["Thx_s_out"], qp=qhx_p, qs=qhx_s)
        
        df.loc[df.index[idx], 'epsilon'] = estimated_epsilon
    except:
        pass
    
    result = pd.DataFrame({
        'Thx_p_out': Thx_p_out,
        'Thx_s_out': Thx_s_out,
        'epsilon': epsilon,
        'qhx_s': qhx_s
    }, index=[0])
    

    logger.info(f"Finished iteration {idx} / {idx_end}, elapsed time: {time.time()-start_time:.2f} s")
    
    df_mod = pd.concat([df_mod, result], ignore_index=True)    

/tmp/ipykernel_87088/3253510504.py:5: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

2024-05-09 15:26:19.817 | INFO     | __main__:<module>:41 - Finished iteration 23 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:19.822 | INFO     | __main__:<module>:41 - Finished iteration 24 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:19.827 | INFO     | __main__:<module>:41 - Finished iteration 25 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:19.834 | INFO     | __main__:<module>:41 - Finished iteration 26 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:19.842 | INFO     | __main__:<module>:41 - Finished iteration 27 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:19.847 | INFO     | __main__:<module>:41 - Finished iteration 28 / 1280, elapsed time: 0.00 s
2024-05-09 15:26:

In [17]:
# Generate visualization

# Load plot configuration
with open(config_path / 'plt_config_heat_exchanger.json') as f:
    plt_config = json.load(f)

# Sync model index with measured data
df_mod.index = df.index[idx_start:idx if idx < idx_end - 1 else idx_end]

fig = experimental_results_plot(plt_config, df, df_comp=[df_mod], vars_config=vars_config, resample=resample_figures)

# Save figure
save_figure(
    figure_name=f"{date_str}_heat_exchanger_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'heat_exhanger_validation_{df.index[0].strftime("%Y%m%d")}')
# )

2024-05-09 15:26:30.978 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:26:30.979 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qhx_p
2024-05-09 15:26:30.984 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace q<sub>hx,p</sub> (m<sup>3</sup>/h) added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:26:30.986 | DEBUG    | phd_visualizations.test_timeseries:experimental_results_plot:700 - Adding trace qhx_s to right yaxis 2
2024-05-09 15:26:30.986 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qhx_s
2024-05-09 15:26:30.988 | WARNING  | phd_visualizations.test_timeseries:add_trace:136 - Index of comparison dataframe 0 is not the same as the main dataframe, filling difference with NaNs
2024-05-09 15:26:31.000 | INFO     | phd_visualizations.test_timeseries:add_

## MED

In [18]:
import MED_model
import matlab

MED_model_matlab = MED_model.initialize()
logger.info('MATLAB engine initialized')
    
idx_start = 0
idx_end = len(df)
df_mod = pd.DataFrame()

# Run model
for idx in range(idx_start,idx_end):
    ds = df.iloc[idx]
    start_time = time.time()

    Tmed_c_out = ds["Tmed_c_out"]
    Tmed_c_in = ds["Tmed_c_in"]
    mmed_f = ds["qmed_f"] if abs(ds["qmed_f"]-5) > 0.5 else 5
    mmed_f = within_range_or_nan_or_max(mmed_f, range=(5, 9), var_name="qmed_f")
    mmed_s = within_range_or_zero_or_max(ds["qmed_s"], range=(30, 48), var_name="qmed_s")
    Tmed_s_in = within_range_or_nan_or_max(ds["Tmed_s_in"], range=(60, 75), var_name="Tmed_s_in")

    MsIn = matlab.double([mmed_s / 3.6], size=(1, 1))  # m³/h -> L/s
    TsinIn = matlab.double([Tmed_s_in], size=(1, 1))
    MfIn = matlab.double([mmed_f], size=(1, 1))
    TcwinIn = matlab.double([Tmed_c_in], size=(1, 1))
    op_timeIn = matlab.double([0], size=(1, 1))
                
    med_model_solved = False
    mmed_d = np.nan
    Tmed_s_out = np.nan
    mmed_c = np.nan
    while not med_model_solved and (Tmed_c_in < Tmed_c_out < 40) and mmed_f > 0 and mmed_s > 0 and Tmed_s_in > 0 and Tmed_s_in > 0:   
        # try:                     
        TcwoutIn = matlab.double([Tmed_c_out], size=(1, 1))
    
        mmed_d, Tmed_s_out, mmed_c, _, _ = MED_model_matlab.MED_model(
            MsIn,  # L/s
            TsinIn,  # ºC
            MfIn,  # m³/h
            TcwoutIn,  # ºC
            TcwinIn,  # ºC
            op_timeIn,  # hours
            nargout=5
        )

        if mmed_c > 20:
            Tmed_c_out = Tmed_c_out + 1
        elif mmed_c < 9:
            Tmed_c_out = Tmed_c_out - 1
        else:
            med_model_solved = True
            
    logger.info(f"Iteration {idx} / {len(df)}. Elapsed time: {time.time()-start_time:.2f} seconds")
    
    result = pd.DataFrame(
        {
            "qmed_f": mmed_f,
            "qmed_d": mmed_d,
            "qmed_c": mmed_c,
            "qmed_s": mmed_s,
            "Tmed_s_in": Tmed_s_in,
            "Tmed_s_out": Tmed_s_out,
            "Tmed_c_in": ds["Tmed_c_in"],
            "Tmed_c_out": Tmed_c_out,
        },
        index=[0]
    )
    
    df_mod = pd.concat([df_mod, result], ignore_index=True)

2024-05-09 15:27:14.292 | INFO     | __main__:<module>:5 - MATLAB engine initialized
2024-05-09 15:27:14.295 | DEBUG    | solarMED_modeling.data_validation:within_range_or_nan_or_max:58 - (qmed_f) Value 0.86 is less than 5.00 -> 0.0
2024-05-09 15:27:14.296 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (qmed_s) Value 0.03 is less than 30.00 -> 0.0
2024-05-09 15:27:14.297 | DEBUG    | solarMED_modeling.data_validation:within_range_or_nan_or_max:58 - (Tmed_s_in) Value 29.26 is less than 60.00 -> 0.0
2024-05-09 15:27:14.301 | INFO     | __main__:<module>:54 - Iteration 0 / 1280. Elapsed time: 0.01 seconds
2024-05-09 15:27:14.302 | DEBUG    | solarMED_modeling.data_validation:within_range_or_nan_or_max:58 - (qmed_f) Value 0.85 is less than 5.00 -> 0.0
2024-05-09 15:27:14.303 | DEBUG    | solarMED_modeling.data_validation:within_range_or_zero_or_max:47 - (qmed_s) Value 0.03 is less than 30.00 -> 0.0
2024-05-09 15:27:14.304 | DEBUG    | solarMED_modeling.data

In [19]:
# Load plot configuration
with open(config_path / 'plt_config_med.json') as f:
    plt_config = json.load(f)

# Sync model index with measured data
df_mod.index = df.index[idx_start:idx if idx < idx_end - 1 else idx_end]

fig = experimental_results_plot(plt_config, df, df_comp=df_mod, vars_config=vars_config, resample=resample_figures)

# Save figure
save_figure(
    figure_name=f"{date_str}_MED_validation", 
    figure_path=attachments_folder,
    fig=fig, formats=('svg', 'html'),
    width=fig.layout.width, height=fig.layout.height, scale=2
)

# fig.show(
#     config=generate_plotly_config(fig, figure_name=f'{df.index[0].strftime("%Y%m%d")}_med_validation')
# )

2024-05-09 15:28:05.687 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-05-09 15:28:05.697 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qmed_f
2024-05-09 15:28:05.715 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace q<sub>med,f</sub> (m<sup>3</sup>/h) added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:28:05.717 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qmed_d
2024-05-09 15:28:05.735 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace q<sub>med,d</sub> (m<sup>3</sup>/h) added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-05-09 15:28:05.737 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add qmed_c
2024-05-09 15:28:05.754 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Tra

In [11]:

# text = []
# for key, value in model.model_dump_configuration().items():
#     if isinstance(value, dict):
#         # Format the dict nicely
#         text.append(f"{key}:\n")
#         for k, v in value.items():
#             text.append(f"  {k}: {v}\n")
#     else:
#         text.append(f"{key}: {value}\n")




# print(text)

lims_mts_src: (0.95, 20)
lims_msf: (4.7, 14)
lims_mmed_s: (30, 48)
lims_mmed_f: (5, 9)
lims_mmed_c: (8, 21)
lims_Tmed_s_in: (60, 75)
lims_Tsf_out: (65, 120.0)
lims_T_hot: (0, 120.0)
use_models: True
use_finite_state_machine: False
sample_time: 30.0
resolution_mode: simple
vacuum_duration_time: 300
brine_emptying_time: 180
startup_duration_time: 60
med_actuators: [{'id': 'med_brine_pump', 'coefficients': [0.010371467694486103, -0.025160600483389525, 0.03393870518526908]}, {'id': 'med_feed_pump', 'coefficients': [0.7035299527191431, -0.09466303549610014, 0.019077706335712326]}, {'id': 'med_distillate_pump', 'coefficients': [4.149635559273511, -3.6572156762250954, 0.9484207971761789]}, {'id': 'med_cooling_pump', 'coefficients': [5.2178993694785625, -0.9238542100009888, 0.056680794931454774]}, {'id': 'med_heatsource_pump', 'coefficients': [0.031175213554380448, -0.01857544733009508, 0.0013320144040346285]}]
ts_actuators: [{'id': 'ts_src_pump', 'coefficients': [0.0, 0.0, 0.0, 0.0, 0.0]}]
UA

## Build report

In [22]:
configuration_text = "".join([f"`{key}`: `{value}`\n" for key, value in model.model_dump_configuration().items()])

In [12]:
test_report = f"""

---
Generated at {datetime.datetime.now().strftime("%Y-%m-%d %H:%M")}
Sample rate: {sample_rate}

Model parameters:
{configuration_text}
---

# Solar MED model validation report for test {date_str}

Validation report for Solar MED model, it includes validation graphs for the individual [component models](#Components) as well as the [complete system](#Complete system).

For the different visualizations, a static version if shown here, but an interactive `html` version is also available that can be opened in any browser. The link to it is shown above the static image.

# Test visualization

[Interactive version](attachments/{date_str}_solarMED_visualization.html)
![Test representation](attachments/{date_str}_solarMED_visualization.svg)

# Components

## Solar field

More detailed information about the model can be found in the [model documentation](../../models/solar_field.md).

- Parameters

| Parameter | Value |
| --------- | ----- |
| β (m)     |  {model.beta_sf:.2e}     |
| H (W/m²)? |  {model.H_sf:.2f}     |

### Temperature prediction

- Performance metrics

| Metric | Value |
| ------ | ----- |
| IAE    |       |
| RMSE   |       |
| ITAE   |       |
| MAE    |       |


[Interactive version](attachments/{date_str}_solar_field_validation.html)
![Solar field validation](attachments/{date_str}_solar_field_validation.svg)

### Inverse (flow prediction)


- Performance metrics

| Metric | Value |
| ------ | ----- |
| IAE    |       |
| RMSE   |       |
| ITAE   |       |
| MAE    |       |

[Interactive version](attachments/{date_str}_solar_field_inverse_validation.html)
![Solar_field_inverse validation](attachments/{date_str}_solar_field_inverse_validation.svg)

## Heat exchanger

More detailed information about the model can be found in the [model documentation](../../models/heat_exchanger.md).

- Parameters

| Parameter | Value |
| --------- | ----- |
| UA (W/K)  | {model.UA_hx:.2e}      |
| H (W/m²)? | {model.H_hx:.2f}     |

- Performance metrics

| Metric | Value |
| ------ | ----- |
| IAE    |       |
| RMSE   |       |
| ITAE   |       |
| MAE    |       |

[Interactive version](attachments/{date_str}_heat_exchanger_validation.html)
![solar MED validation](attachments/{date_str}_heat_exchanger_validation.svg)

## Thermal storage

More detailed information about the model can be found in the [model documentation](../../models/thermal_storage.md).

- Parameters

| Parameter    | Top        | Medium     | Bottom     |
| ------------ | ---------- | ---------- | ---------- |
| $UA_h$ (W/K) | {model.UAts_h[0]:.2e} | {model.UAts_h[1]:.2e} | {model.UAts_h[2]:.2e} |
| $V_h$ (m³)   | {model.Vts_h[0]:.2f} | {model.Vts_h[1]:.2f} | {model.Vts_h[2]:.2f} |
| $UA_c$ (W/K) | {model.UAts_c[0]:.2e} | {model.UAts_c[1]:.2e} | {model.UAts_c[2]:.2e} |
| $V_c$ (m³)   | {model.Vts_c[0]:.2f} | {model.Vts_c[1]:.2f} | {model.Vts_c[2]:.2f} |

- Performance metrics

| Metric | Value |
| ------ | ----- |
| IAE    |       |
| RMSE   |       |
| ITAE   |       |
| MAE    |       |

[Interactive version](attachments/{date_str}_thermal_storage_validation.html)
![Thermal storage validation](attachments/{date_str}_thermal_storage_validation.svg)

## MED

More detailed information about the model can be found in the [model documentation](../../models/MED.md).

- Parameters


- Performance metrics

| Metric | Value |
| ------ | ----- |
| IAE    |       |
| RMSE   |       |
| ITAE   |       |
| MAE    |       |

[Interactive version](attachments/{date_str}_MED_validation.html)
![MED validation](attachments/{date_str}_MED_validation.svg)

# Complete system

More detailed information about the model can be found in the [model documentation](../../models/complete_system.md).

(For some reason the static image generation is broken, but the interactive version is displayed correctly)

[Interactive version](attachments/{date_str}_solarMED_validation.html)
![solar MED validation](attachments/{date_str}_solarMED_validation.svg)

### State evolution

Result of Finiste State Machines (FSMs) evaluation:

[Interactive version](attachments/{date_str}_solarMED_FSMs.html)
![solar MED FSMs](attachments/{date_str}_solarMED_FSMs.svg)

"""

## Build presentation report

In [40]:
df.index[step_idx]

df_mod_copy.iloc[step_idx]

current_sample        1257
wmed_f                  35
Tamb              32.58851
I                  65.2538
Tmed_c_in             27.9
                    ...   
qmed_b                 0.0
qhx_p             8.865818
qhx_s                  0.0
q3wv_src               0.0
q3wv_dis               0.0
Name: 1256, Length: 82, dtype: object

In [44]:
operating_modes_anim_str = "".join(
    [
f"""<grid drag="100 10" drop="top" bg="whitesmoke">
**Operating mode at step {step_idx} ({df.index[step_idx].strftime('%Y-%m-%d %H:%M')})**
</grid>
<grid drag="100 16" drop="0 12" bg="whitesmoke">
**Place holder for plot at step {step_idx}**
</grid>
<grid drag="100 70" drop="bottom" bg="whitesmoke"> 
![Operating mode step X](../../operating_modes/{df_mod_copy.iloc[step_idx]['current_state'].name}.svg) 
</grid>\n
""" for step_idx in range(0, len(df)-len(df)%30, len(df)%30)
    ]
)

In [49]:
test_presentation = f"""---
generated_at: {datetime.datetime.now().strftime("%Y-%m-%d %H:%M")}
sample_rate: {sample_rate}
margin: 0.05
transition: none
maxScale: 2
width: 1000
height: 750
---

---
%% Model parameters: %%
{configuration_text}
---

<style>
	.with-blue-border{{
		border: 1px solid blue;
	}}
	
	.with-border{{
		border: 1px solid red;
	}}

	 .scaled_to_zoom{{
		 zoom: 0.7; 
	    -moz-transform: scale(0.7); 
	    -moz-transform-origin: 0 0;
	 }}
	 
	 .scaled_iframe{{
        -ms-zoom: 0.75;
        -moz-transform: scale(0.75);
        -moz-transform-origin: 0 0;
        -o-transform: scale(0.75);
        -o-transform-origin: 0 0;
        -webkit-transform: scale(0.75);
        -webkit-transform-origin: 0 0;
	}}
</style>


# Solar MED model validation report 
## test {date_str}

---
## Index

- Context
    - Nomenclature
    - Decision variables description
    - Environment variables description
    - Objective function
- Test visualization
- Components validation
- Solar field
	- Temperature prediction
	- Flow prediction
- Heat exchanger
- Thermal storage
- MED
- Complete system validation
	- Model
	- State evolution visualization

---
## Context.

Poner algún texto introductorio del proceso

--

## Context. Nomenclature

![solarMED_diagram](../../models/attachments/solarMED_optimization-general_diagram.svg)
[Nomenclature](../../Nomenclature.md)

--
### Context. Decision variables description

::: block <!-- element style="font-size:8pt-->


|            Variable             | Description                                                       | Unidades | Observations     |
| :-----------------------------: | ----------------------------------------------------------------- | :------: | ---------------- |
|        $T_{{med,s,in}}^*$         | (float+bool) MED heat source inlet temperature                    |    ºC    |                  |
|          $q_{{med,s}}^*$          | (float) MED heat source flow rate                                 |   m³/h   |                  |
|          $q_{{med,f}}^*$          | (float) MED feed water flow rate                                  |   m³/h   |                  |
|        $T_{{med,c,out}}^*$        | (float) MED condenser outlet temperature                          |    ºC    |                  |
|         $T_{{sf,out}}^*$          | (float+bool) Solar field outlet temperature                       |    ºC    |                  |
|           $q_{{ts}}^*$            | (float+bool) Thermal storage heat source re-circulation flow rate |   m³/h   |                  |
| $\textrm{{MED}}_{{vacuum,state}}^*$ | (int) MED vacuum system state: 0-OFF, 1-LOW, 2-HIGH               |    -     | Defaults to HIGH |
|                                 | **TOTAL**                                                         |    -     |                  |
:::

--
### Context. Environment variables description

|    Variable    | Descripción          | Unidades |
| :------------: | -------------------- | :------: |
|      $I$       | Solar irradiance     |   W/m²   |
|   $T_{{amb}}$    | Ambient temperature  |    ºC    |
| $T_{{med,c,in}}$ | Seawater temperature |    ºC    |

--
## Context. Objective function

- Economic cost function:
$$ J = \min\limits_{{\Delta z}} \left( C_{{e}}\left[\frac{{u.m.}}{{kWh}}\right]·J_{{e}} [kW] - C_{{w}}\left[\frac{{u.m.}}{{m^3}} \right]·q_{{med,d}} \left[ \frac{{m^3}}{{h}} \right]\right)·t_{{s}} \: \left[ u.m. \right] $$

Where the electricity consumption is obtained as the sum of every individual consumption:

$$J_{{e}} = f(J_{{med,vacuum}}, J_{{med,s}}, J_{{med,f}}, J_{{med,c}}, J_{{med,d}}, J_{{med,b}}, J_{{sf}}, J_{{ts,src}})$$

$$ J_{{e}} = \sum\limits_{{i=1}}^{{N}}J_{{i}} $$

---
<grid drag="100 10" drop="top">
## Test visualization
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_solarMED_visualization.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

---
Components validation
--
Components validation. Solar field diagram

![Solar field diagram](../../models/attachments/solarMED_optimization-solar_field.drawio.svg)

--
<grid drag="100 10" drop="top">
## Components validation. Solar field results. Temperature prediction

More detailed information about the model can be found in the [model documentation](../../models/solar_field.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_solar_fieldvalidation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

--
<grid drag="100 10" drop="top">
## Components validation. Solar field results. Flow prediction

More detailed information about the model can be found in the [model documentation](../../models/solar_field.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_solar_field_inverse_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

--
Components validation. Heat exchanger diagram

![Heat exchanger diagram](../../models/attachments/solarMED_optimization-Heat_exchanger.svg)

--
<grid drag="100 10" drop="top">
## Components validation. Heat exhanger results

More detailed information about the model can be found in the [model documentation](../../models/heat_exchanger.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_heat_exchanger_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

--
Components validation. Thermal storage diagram

![thermal storage diagram](../../models/attachments/solarMED_optimization-Storage model.drawio.svg)

--
<grid drag="100 10" drop="top">
## Components validation. Thermal storage results

More detailed information about the model can be found in the [model documentation](../../models/thermal_storage.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_thermal_storage_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>
--
Components validation. MED diagram

Pendiente: Poner un diagrama guapete

![thermal storage diagram](../../models/attachments/solarMED_optimization-Storage model.drawio.svg)
--
<grid drag="100 10" drop="top">
## Components validation. MED results

More detailed information about the model can be found in the [model documentation](../../models/MED.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_MED_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

---
# Complete system validation
--
Complete system validation. System diagram

![solarMED_diagram](../../models/attachments/solarMED_optimization-general_diagram.svg)
--
<grid drag="100 10" drop="top">
### Complete system validation. Results

More detailed information about the model can be found in the [model documentation](../../models/complete_system.md).
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_solarMED_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

--

<grid drag="100 10" drop="top">
## Complete system validation. States evolution.

Result of Finiste State Machines (FSMs) evaluation
</grid>

<grid drop="bottom" drag="100 85">
<iframe width="100%" height="100%" data-src="attachments/{date_str}_solarMED_validation.html"></iframe>
<!-- element style="width:100%; height:100%" -->
</grid>

--
{operating_modes_anim_str}
--

### Context. States description
::: block <!-- element class="" style="font-size:14pt;" grid="drop:bottom"-->

### Solar field

- **Idle**. Passive state. In this state no fluid is circulating through the solar field and there are just losses to the environment.
- **Active**. Fluid is circulating through the solar field.

### Thermal storage

- **Idle**. Passive state. In this state is always discharging, it may just be losing heat to the environment (slow discharge), or releasing its heat to the load (fast discharge). 
- **Active**. Recirculating state. In this state water from the tanks gets heated in the heat exchanger.

### MED

- **Off**. No vacuum, nor heat or cooling. No distillate produced.
- **Generating vacuum**. Generating vacuum (high state), no heat nor cooling. No distillate produced.
- **Idle**. Vacuum in low state, plant not using heat nor cooling. No distillate produced
- **Starting-up**. Vacuum in low state, plant using heat and cooling. No distillate produced. Its duration is a function of the initial starting point.
- **Active**. Vacuum in low state and plant using heat and cooling to produce distillate.
- **Shutting-down**. Vacuum off, plant not using heat or cooling, no distillate produced, brine pump active.
:::

"""

In [50]:
# Save report

# _at_{datetime.datetime.now().strftime("%Y%m%dT%H%M")}
with open(output_folder / f'{date_str}_solarMED_validation_report.md', 'w') as f:
    f.write(test_report)
    
with open(output_folder / f'{date_str}_solarMED_validation_presentation.md', 'w') as f:
    f.write(test_presentation)